In [1]:
import os
os.environ["BEEP_ENV"] = "dev"
os.environ["BEEP_PROCESSING_DIR"] ="data_transfer"
data_dir = "./data_transfer"

In [2]:
import pandas as pd
import numpy as np
import glob
import json
from datetime import datetime
from matplotlib import pyplot as plt
from monty.serialization import loadfn
from beep import structure, featurize

In [3]:
def get_time(d):
    ds = d.split(".")
    x = datetime.strptime(ds[0], '%Y-%m-%d %H:%M:%S')
    return x.timestamp() + float('.' + (ds[1]))

In [4]:
data_dir = "./data_transfer"
file_list = glob.glob(os.path.join(data_dir, '*timeseries.csv'))
file_list = [f for f in file_list if "LFP" in f]
file_list

['./data_transfer\\SNL_18650_LFP_15C_0-100_0.5-1C_a_timeseries.csv',
 './data_transfer\\SNL_18650_LFP_15C_0-100_0.5-1C_b_timeseries.csv',
 './data_transfer\\SNL_18650_LFP_15C_0-100_0.5-2C_a_timeseries.csv',
 './data_transfer\\SNL_18650_LFP_15C_0-100_0.5-2C_b_timeseries.csv',
 './data_transfer\\SNL_18650_LFP_25C_0-100_0.5-0.5C_a_timeseries.csv',
 './data_transfer\\SNL_18650_LFP_25C_0-100_0.5-1C_a_timeseries.csv',
 './data_transfer\\SNL_18650_LFP_25C_0-100_0.5-1C_b_timeseries.csv',
 './data_transfer\\SNL_18650_LFP_25C_0-100_0.5-1C_c_timeseries.csv',
 './data_transfer\\SNL_18650_LFP_25C_0-100_0.5-1C_d_timeseries.csv',
 './data_transfer\\SNL_18650_LFP_25C_0-100_0.5-2C_a_timeseries.csv',
 './data_transfer\\SNL_18650_LFP_25C_0-100_0.5-2C_b_timeseries.csv',
 './data_transfer\\SNL_18650_LFP_25C_0-100_0.5-3C_a_timeseries.csv',
 './data_transfer\\SNL_18650_LFP_25C_0-100_0.5-3C_b_timeseries.csv',
 './data_transfer\\SNL_18650_LFP_25C_0-100_0.5-3C_c_timeseries.csv',
 './data_transfer\\SNL_18650_LFP

In [ ]:
file_list = glob.glob(os.path.join(data_dir, '*timeseries.csv'))
file_list = [f for f in file_list if "LFP" in f]
column_rename = {'Date_Time': 'datetime', 'Test_Time (s)':'test_time', 
                   'Cycle_Index':'cycle_index', 'Current (A)':'current',
                   'Voltage (V)':'voltage', 
                   'Charge_Capacity (Ah)':'charge_capacity',
                   'Discharge_Capacity (Ah)':'discharge_capacity',
                   'Charge_Energy (Wh)':'charge_energy', 
                   'Discharge_Energy (Wh)':'discharge_energy', 
                   'Cell_Temperature (C)':'temperature'}

new_dtypes = {'datetime': np.float32, 'test_time':np.float32, 
              'step_index':np.int16,
              'cycle_index': np.int32, 'current':np.float32,
              'voltage': np.float32, 
              'charge_capacity': np.float64,
              'discharge_capacity': np.float64,
              'charge_energy':np.float64, 
              'discharge_energy':np.float64, 
              'temperature':np.float32}
i = 0
for f in file_list:
    df = pd.read_csv(f)
    df = df.rename(columns=column_rename)
    df['step_index'] = 0
    df.datetime = df.datetime.apply(lambda x: get_time(x))
    df = df.astype(new_dtypes).drop('Environment_Temperature (C)', axis=1)
    if i < 10:
        j = "0" + str(i)
    else:
        j = str(i)
    new_name = "_".join(test.split("_")[3:8])+ "_CH"+ j
    df.to_csv("./data_transfer/%s.csv" %new_name, index=False)
    i += 1

In [9]:
# import warnings
# warnings.filterwarnings("ignore")

In [14]:
file_list = glob.glob(os.path.join(data_dir, '*[0-9].csv'))
for f in file_list:
    print(f)
    raw_cycler_run = structure.RawCyclerRun.from_file(f)
    #raw_cycler_run.data = raw_cycler_run.data.dropna()
    processed_cycler_run = structure.ProcessedCyclerRun.from_raw_cycler_run(raw_cycler_run, [2.8, 3.5])
    
    #featurize 
    featurizer_DeltaQ = featurize.DeltaQFastCharge.from_run(input_filename='dummy.json', feature_dir='.', processed_cycler_run=processed_cycler_run)
    
    #export json file in correct format
    featurize_deltaQ_dict = {"@module": "beep.featurize", "@class": "DeltaQFastCharge"}
    featurize_deltaQ_dict["name"] = ('\\'.join(featurizer_DeltaQ.name.split("\\")[:-1]) +"\\" 
                                     + f.split("\\")[1][:-4] + "_features_DeltaQFastCharge.json")
    X_dict = {}
    for i in list(featurizer_DeltaQ.X.columns):
        X_dict[i] = [featurizer_DeltaQ.X.loc[0, i].astype(np.float64)]
    featurize_deltaQ_dict["X"] = X_dict
    featurize_deltaQ_dict["metadata"] = featurizer_DeltaQ.metadata
    featurize_deltaQ_dict["@version"] = "2021.1.11.15"
    json.dump(featurize_deltaQ_dict, open(featurize_deltaQ_dict['name'], 'w'))
    
    
    #export trajectory data
    featurize_Trajectory = featurize.TrajectoryFastCharge.from_run(input_filename=f.split("\\")[1][:-4] + '.json', 
                                                                   feature_dir='.', processed_cycler_run=processed_cycler_run)
    featurize_Trajectory_dict = {"@module": "beep.featurize", "@class": "TrajectoryFastCharge"}
    featurize_Trajectory_dict["name"] = ('\\'.join(featurize_Trajectory.name.split("\\")[:-1]) +"\\"+
                                         f.split("\\")[1][:-4] + "_features_TrajectoryFastCharge.json")
    X_dict = {}
    for i in list(featurize_Trajectory.X.columns):
        X_dict[i] = [featurize_Trajectory.X.loc[0, i].astype(np.float64)]
    featurize_Trajectory_dict["X"] = X_dict
    featurize_Trajectory_dict["metadata"] = featurize_Trajectory.metadata
    featurize_Trajectory_dict["@version"] = "2021.1.11.15"
    json.dump(featurize_Trajectory_dict, open(featurize_Trajectory_dict['name'], 'w'))
    

./data_transfer\LFP_15C_0-100_0.5-1C_a_CH00.csv


--- Logging error ---
Traceback (most recent call last):
  File "c:\users\mattm\appdata\local\programs\python\python36\lib\logging\__init__.py", line 992, in emit
    msg = self.format(record)
  File "c:\users\mattm\appdata\local\programs\python\python36\lib\logging\__init__.py", line 838, in format
    return fmt.format(record)
  File "c:\users\mattm\appdata\local\programs\python\python36\lib\logging\__init__.py", line 578, in format
    s = self.formatMessage(record)
  File "c:\users\mattm\appdata\local\programs\python\python36\lib\logging\__init__.py", line 547, in formatMessage
    return self._style.format(record)
  File "c:\users\mattm\appdata\local\programs\python\python36\lib\logging\__init__.py", line 391, in format
    return self._fmt % record.__dict__
KeyError: 'service'
Call stack:
  File "c:\users\mattm\appdata\local\programs\python\python36\lib\runpy.py", line 193, in _run_module_as_main
    "__main__", mod_spec)
  File "c:\users\mattm\appdata\local\programs\python\pytho

  1%|▋                                                                               | 38/4550 [00:02<04:38, 16.23it/s]

  1%|▋                                                                               | 40/4550 [00:02<04:44, 15.87it/s]

  1%|▋                                                                               | 42/4550 [00:02<04:38, 16.19it/s]

  1%|▊                                                                               | 44/4550 [00:02<04:32, 16.51it/s]

  1%|▊                                                                               | 46/4550 [00:02<04:29, 16.70it/s]

  1%|▊                                                                               | 48/4550 [00:02<04:39, 16.11it/s]

  1%|▉                                                                               | 50/4550 [00:02<04:33, 16.45it/s]

  1%|▉                                                                               | 52/4550 [00:03<04:42, 15.95it/s]

  1%|▉                          

  4%|██▉                                                                            | 166/4550 [00:10<04:33, 16.06it/s]

  4%|██▉                                                                            | 168/4550 [00:10<04:26, 16.45it/s]

  4%|██▉                                                                            | 170/4550 [00:10<04:23, 16.64it/s]

  4%|██▉                                                                            | 172/4550 [00:10<04:31, 16.15it/s]

  4%|███                                                                            | 174/4550 [00:10<04:26, 16.44it/s]

  4%|███                                                                            | 176/4550 [00:11<04:23, 16.61it/s]

  4%|███                                                                            | 178/4550 [00:11<04:31, 16.13it/s]

  4%|███▏                                                                           | 180/4550 [00:11<04:37, 15.77it/s]

  4%|███▏                       

  6%|█████                                                                          | 294/4550 [00:18<04:22, 16.20it/s]

  7%|█████▏                                                                         | 296/4550 [00:18<04:18, 16.45it/s]

  7%|█████▏                                                                         | 298/4550 [00:18<04:14, 16.72it/s]

  7%|█████▏                                                                         | 300/4550 [00:18<04:12, 16.85it/s]

  7%|█████▏                                                                         | 302/4550 [00:18<04:10, 16.94it/s]

  7%|█████▎                                                                         | 304/4550 [00:18<04:20, 16.29it/s]

  7%|█████▎                                                                         | 306/4550 [00:19<04:15, 16.60it/s]

  7%|█████▎                                                                         | 308/4550 [00:19<04:23, 16.08it/s]

  7%|█████▍                     

...

 16%|████████████▊                                                                 | 592/3597 [00:08<00:54, 55.44it/s]

 17%|████████████▉                                                                 | 599/3597 [00:08<01:05, 45.45it/s]

 17%|█████████████                                                                 | 605/3597 [00:09<01:14, 40.37it/s]

 17%|█████████████▏                                                                | 611/3597 [00:09<01:19, 37.43it/s]

 17%|█████████████▎                                                                | 616/3597 [00:09<01:23, 35.62it/s]

 17%|█████████████▍                                                                | 621/3597 [00:09<01:21, 36.68it/s]

 17%|█████████████▌                                                                | 626/3597 [00:09<01:24, 35.14it/s]

 18%|█████████████▋                                                                | 631/3597 [00:09<01:21, 36.38it/s]

 18%|█████████████▊                     

 34%|██████████████████████████                                                   | 1217/3597 [00:18<00:29, 81.87it/s]

 34%|██████████████████████████▎                                                  | 1229/3597 [00:18<00:26, 88.62it/s]

 34%|██████████████████████████▌                                                  | 1239/3597 [00:18<00:31, 73.96it/s]

 35%|██████████████████████████▊                                                  | 1252/3597 [00:18<00:28, 80.98it/s]

 35%|██████████████████████████▉                                                  | 1261/3597 [00:18<00:32, 72.19it/s]

 35%|███████████████████████████▎                                                 | 1274/3597 [00:19<00:27, 83.12it/s]

 36%|███████████████████████████▍                                                 | 1284/3597 [00:19<00:32, 71.19it/s]

 36%|███████████████████████████▋                                                 | 1293/3597 [00:19<00:43, 53.42it/s]

 36%|███████████████████████████▊       

 54%|█████████████████████████████████████████▎                                   | 1929/3597 [00:27<00:19, 85.37it/s]

 54%|█████████████████████████████████████████▌                                   | 1940/3597 [00:27<00:21, 77.59it/s]

 54%|█████████████████████████████████████████▋                                   | 1949/3597 [00:27<00:21, 75.83it/s]

 54%|█████████████████████████████████████████▉                                   | 1960/3597 [00:27<00:20, 79.12it/s]

 55%|██████████████████████████████████████████▏                                  | 1971/3597 [00:27<00:19, 84.53it/s]

 55%|██████████████████████████████████████████▍                                  | 1982/3597 [00:28<00:18, 86.54it/s]

 55%|██████████████████████████████████████████▋                                  | 1992/3597 [00:28<00:19, 81.26it/s]

 56%|██████████████████████████████████████████▉                                  | 2005/3597 [00:28<00:18, 86.97it/s]

 56%|███████████████████████████████████

 76%|██████████████████████████████████████████████████████████▏                  | 2720/3597 [00:36<00:08, 97.61it/s]

 76%|█████████████████████████████████████████████████████████▊                  | 2735/3597 [00:36<00:08, 103.40it/s]

 76%|██████████████████████████████████████████████████████████▊                  | 2748/3597 [00:37<00:09, 91.73it/s]

 77%|███████████████████████████████████████████████████████████                  | 2759/3597 [00:37<00:09, 86.98it/s]

 77%|███████████████████████████████████████████████████████████▎                 | 2769/3597 [00:37<00:10, 75.74it/s]

 77%|███████████████████████████████████████████████████████████▌                 | 2781/3597 [00:37<00:10, 80.86it/s]

 78%|███████████████████████████████████████████████████████████▊                 | 2792/3597 [00:37<00:09, 85.92it/s]

 78%|███████████████████████████████████████████████████████████▉                 | 2802/3597 [00:37<00:09, 80.88it/s]

 78%|███████████████████████████████████

 93%|███████████████████████████████████████████████████████████████████████▊     | 3354/3597 [00:45<00:04, 52.58it/s]

 93%|███████████████████████████████████████████████████████████████████████▉     | 3360/3597 [00:45<00:04, 49.16it/s]

 94%|████████████████████████████████████████████████████████████████████████     | 3366/3597 [00:46<00:04, 51.45it/s]

 94%|████████████████████████████████████████████████████████████████████████▎    | 3378/3597 [00:46<00:03, 59.77it/s]

 94%|████████████████████████████████████████████████████████████████████████▍    | 3386/3597 [00:46<00:03, 60.98it/s]

 94%|████████████████████████████████████████████████████████████████████████▋    | 3395/3597 [00:46<00:03, 63.92it/s]

 95%|████████████████████████████████████████████████████████████████████████▊    | 3403/3597 [00:46<00:02, 66.44it/s]

 95%|█████████████████████████████████████████████████████████████████████████    | 3412/3597 [00:46<00:02, 68.02it/s]

 95%|███████████████████████████████████

In [13]:
'\\'.join(featurize_Trajectory.name.split("\\")[:-1]) +"\\"+ f.split("\\")[1][:-4] + "_features_TrajectoryFastCharge.json"

'C:\\Users\\mattm\\Documents\\CalPoly\\DATA 451\\Toyota\\TrajectoryFastCharge\\LFP_15C_0-100_0.5-1C_a_CH01_features_TrajectoryFastCharge.json'

In [46]:
featurizer_DeltaQ = featurize.DeltaQFastCharge.from_run(input_filename='dummy.json', feature_dir='.', processed_cycler_run=processed_cycler_run)
featurizer_DeltaQ.X

c:\users\mattm\appdata\local\programs\python\python36\lib\site-packages\beep\featurize.py:1044: RuntimeWarning: All-NaN axis encountered
  X[17] = np.nanmin(IR_trend)


discharge_capacity_cycle_2  max_discharge_capacity_difference  \
0                        1.03                              1.035   

   discharge_capacity_cycle_100  integrated_time_temperature_cycles_1:100  \
0                         1.032                             306697.588291   

   charge_time_cycles_1:5  abs_min_discharge_capacity_difference_cycles_2:100  \
0                  5760.0                                          -0.446806    

   abs_mean_discharge_capacity_difference_cycles_2:100  \
0                                          -2.742859     

   abs_variance_discharge_capacity_difference_cycles_2:100  \
0                                          -3.166992         

   abs_skew_discharge_capacity_difference_cycles_2:100  \
0                                           0.584775     

   abs_kurtosis_discharge_capacity_difference_cycles_2:100  ...  \
0                                           1.867028        ...   

   max_temperature_cycles_1:100  min_temperature_cycles_1:100  \
0                        18.459                         15.16   

   slope_discharge_capacity_cycle_number_2:100  \
0                                    -0.000595   

   intercept_discharge_capacity_cycle_number_2:100  \
0                                         1.072909   

   slope_discharge_capacity_cycle_number_91:100  \
0                                  1.217792e-17   

   intercept_discharge_capacity_cycle_number_91:100  \
0                                             1.032   

   min_internal_resistance_cycles_2:100  internal_resistance_cycle_2  \
0                                   NaN                          NaN   

   internal_resistance_difference_cycles_2:100  nominal_capacity_by_median  
0                                          NaN                       1.033  

[1 rows x 21 columns]

{"@module": "beep.featurize", "@class": "DeltaQFastCharge", "name": "C:\\Users\\mattm\\Documents\\CalPoly\\DATA 451\\Toyota\\data_transfer\\data-share\\features\\DeltaQFastCharge\\SNL_18650_LFP_15C_0-100.5-1C_a_timeseries_CH01_features_DeltaQFastCharge.json", "X": {"discharge_capacity_cycle_2": [1.032], "max_discharge_capacity_difference": [0.968], "discharge_capacity_cycle_100": [1.032], "integrated_time_temperature_cycles_1:100": [378624.0], "charge_time_cycles_1:5": [5760.0], "abs_min_discharge_capacity_difference_cycles_2:100": [-0.44680629485828904], "abs_mean_discharge_capacity_difference_cycles_2:100": [-2.7428591200248187], "abs_variance_discharge_capacity_difference_cycles_2:100": [-3.16699189126899], "abs_skew_discharge_capacity_difference_cycles_2:100": [0.5847754492806106], "abs_kurtosis_discharge_capacity_difference_cycles_2:100": [1.867027981692003], "abs_first_discharge_capacity_difference_cycles_2:100": [-3.309824012313473], "max_temperature_cycles_1:100": [20.0], "min_temperature_cycles_1:100": [20.0], "slope_discharge_capacity_cycle_number_2:100": [-0.0005718738404452728], "intercept_discharge_capacity_cycle_number_2:100": [1.0711290455576175], "slope_discharge_capacity_cycle_number_91:100": [1.217792177277779e-17], "intercept_discharge_capacity_cycle_number_91:100": [1.0319999999999983], "min_internal_resistance_cycles_2:100": [NaN], "internal_resistance_cycle_2": [NaN], "internal_resistance_difference_cycles_2:100": [NaN], "nominal_capacity_by_median": [1.033]}, "metadata": {"barcode": null, "protocol": null, "channel_id": null, "parameters": {"init_pred_cycle": 10, "mid_pred_cycle": 91, "final_pred_cycle": 100, "n_nominal_cycles": 40}}, "@version": "2021.1.11.15"}

In [18]:
featurize_deltaQ_dict = {"@module": "beep.featurize", "@class": "DeltaQFastCharge"}
featurize_deltaQ_dict["name"] = ('\\'.join(featurizer_DeltaQ.name.split("\\")[:-1]) +"\\" 
                                 + file_list[0].split("\\")[1][:-4] + "_features_DeltaQFastCharge.json")
X_dict = {}
for i in list(featurizer_DeltaQ.X.columns):
    X_dict[i] = [featurizer_DeltaQ.X.loc[0, i].astype(np.float64)]
featurize_deltaQ_dict["X"] = X_dict
featurize_deltaQ_dict["metadata"] = featurizer_DeltaQ.metadata
featurize_deltaQ_dict["@version"] = "2021.1.11.15"
json.dump(featurize_deltaQ_dict, open(featurize_deltaQ_dict['name'], 'w'))
featurize_deltaQ_dict

{'@module': 'beep.featurize',
 '@class': 'DeltaQFastCharge',
 'name': 'C:\\Users\\mattm\\Documents\\CalPoly\\DATA 451\\Toyota\\DeltaQFastCharge\\LFP_15C_0-100_0.5-1C_a_CH00_features_DeltaQFastCharge.json',
 'X': {'discharge_capacity_cycle_2': [1.03],
  'max_discharge_capacity_difference': [1.035],
  'discharge_capacity_cycle_100': [1.032],
  'integrated_time_temperature_cycles_1:100': [306697.58829142264],
  'charge_time_cycles_1:5': [5760.0],
  'abs_min_discharge_capacity_difference_cycles_2:100': [-0.44680629485828904],
  'abs_mean_discharge_capacity_difference_cycles_2:100': [-2.7428591200248187],
  'abs_variance_discharge_capacity_difference_cycles_2:100': [-3.16699189126899],
  'abs_skew_discharge_capacity_difference_cycles_2:100': [0.5847754492806106],
  'abs_kurtosis_discharge_capacity_difference_cycles_2:100': [1.867027981692003],
  'abs_first_discharge_capacity_difference_cycles_2:100': [-3.309824012313473],
  'max_temperature_cycles_1:100': [18.458999633789062],
  'min_temper

{"@module": "beep.featurize", "@class": "TrajectoryFastCharge", "name": "C:\\Users\\mattm\\Documents\\CalPoly\\DATA 451\\Practice Notebooks\\data-driven-prediction-of-battery-cycle-life-before-capacity-degradation\\data2\\data-share\\features\\TrajectoryFastCharge\\b3_CH00_features_TrajectoryFastCharge.json", "X": {"capacity_0.98": [522], "capacity_0.95": [815], "capacity_0.92": [900], "capacity_0.89": [943], "capacity_0.86": [972], "capacity_0.83": [999], "capacity_0.8": [1008]}, "metadata": {"barcode": null, "protocol": null, "channel_id": null, "parameters": {"thresh_max_cap": 0.98, "thresh_min_cap": 0.78, "interval_cap": 0.03}}, "@version": "2021.1.11.15"}

In [40]:
featurize_Trajectory = featurize.TrajectoryFastCharge.from_run(input_filename=file_list[0].split("\\")[1][:-4] + '.json', 
                                                                feature_dir='.', processed_cycler_run=processed_cycler_run)
featurize_Trajectory_dict = {"@module": "beep.featurize", "@class": "TrajectoryFastCharge"}
featurize_Trajectory_dict["name"] = featurize_Trajectory.name
# ('\\'.join(featurizer_Trajectory.name.split("\\")[:-1]) +"\\" 
#                                  + file_list[0].split("\\")[1][:-4] + "_features_TrajectoryFastCharge.json")
X_dict = {}
for i in list(featurizer_Trajectory.X.columns):
    X_dict[i] = [featurizer_Trajectory.X.loc[0, i].astype(np.float64)]
featurize_Trajectory_dict["X"] = X_dict
featurize_Trajectory_dict["metadata"] = featurizer_Trajectory.metadata
featurize_Trajectory_dict["@version"] = "2021.1.11.15"
json.dump(featurize_Trajectory_dict, open(featurize_Trajectory_dict['name'], 'w'))
featurize_Trajectory_dict

{'@module': 'beep.featurize',
 '@class': 'TrajectoryFastCharge',
 'name': 'C:\\Users\\mattm\\Documents\\CalPoly\\DATA 451\\Toyota\\TrajectoryFastCharge\\LFP_15C_0-100.5-1C_a_features_TrajectoryFastCharge.json',
 'X': {'capacity_0.98': [506.0],
  'capacity_0.95': [506.0],
  'capacity_0.92': [506.0],
  'capacity_0.89': [4550.0],
  'capacity_0.86': [4550.0],
  'capacity_0.83': [4550.0],
  'capacity_0.8': [4550.0]},
 'metadata': {'barcode': None,
  'protocol': None,
  'channel_id': None,
  'parameters': {'thresh_max_cap': 0.98,
   'thresh_min_cap': 0.78,
   'interval_cap': 0.03}},
 '@version': '2021.1.11.15'}

In [35]:
featurizer_Trajectory = featurize.TrajectoryFastCharge.from_run(input_filename=file_list[0].split("\\")[1][:-4] + '.json', feature_dir='.', processed_cycler_run=processed_cycler_run)
featurizer_Trajectory.name

'C:\\Users\\mattm\\Documents\\CalPoly\\DATA 451\\Toyota\\TrajectoryFastCharge\\LFP_15C_0-100.5-1C_a_features_TrajectoryFastCharge.json'

In [18]:
import json
import glob

# Import beep scripts
from beep import validate, structure, featurize
data_dir = './data_transfer/'

#file_list = glob.glob(os.path.join(data_dir, '.csv'))
file_list = glob.glob(os.path.join(data_dir, '*[0-9].csv'))
print(file_list)

# mode = 'events_off'
# mapped  =  {
#             "mode": 'events_off',  # mode run|test|events_off
#             "file_list": file_list,  # list of file paths ['path/test1.csv', 'path/test2.csv']
#             'run_list': list(range(len(file_list)))  # list of run_ids [0, 1]
#             }
# mapped = json.dumps(mapped)
# #print(mapped)
# #Validation
# validated = validate.validate_file_list_from_json(mapped)
# validated_output = json.loads(validated)
# validated_output['mode'] = mode  # mode run|test|events_off
# validated_output['run_list'] = list(range(len(validated_output['file_list'])))
# validated = json.dumps(validated_output)

# print(validated)

# Data structuring
structured = structure.process_file_list_from_json(validated)
structured_output = json.loads(structured)
structured_output['mode'] = mode  # mode run|test|events_off
structured_output['run_list'] = list(range(len(file_list)))
structured = json.dumps(structured_output)

print(structured)

# Featurization
featurized = featurize.process_file_list_from_json(structured)
featurized_output = json.loads(featurized)
featurized_output['mode'] = mode  # mode run|test|events_off
featurized_output['run_list'] = list(range(len(file_list)))
featurized = json.dumps(featurized_output)


100%|████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00,  1.48it/s]


{"file_list": ["./data_transfer/SNL_18650_LFP_15C_0-100_0.5-1C_a_timeseries_CH01.csv"], "run_list": [0], "validity": ["valid"], "message_list": [{"comment": "", "error": ""}], "mode": "events_off"}


--- Logging error ---
Traceback (most recent call last):
  File "c:\users\mattm\appdata\local\programs\python\python36\lib\logging\__init__.py", line 992, in emit
    msg = self.format(record)
  File "c:\users\mattm\appdata\local\programs\python\python36\lib\logging\__init__.py", line 838, in format
    return fmt.format(record)
  File "c:\users\mattm\appdata\local\programs\python\python36\lib\logging\__init__.py", line 578, in format
    s = self.formatMessage(record)
  File "c:\users\mattm\appdata\local\programs\python\python36\lib\logging\__init__.py", line 547, in formatMessage
    return self._style.format(record)
  File "c:\users\mattm\appdata\local\programs\python\python36\lib\logging\__init__.py", line 391, in format
    return self._fmt % record.__dict__
KeyError: 'service'
Call stack:
  File "c:\users\mattm\appdata\local\programs\python\python36\lib\runpy.py", line 193, in _run_module_as_main
    "__main__", mod_spec)
  File "c:\users\mattm\appdata\local\programs\python\pytho

  5%|███▊                                                                           | 220/4550 [00:27<08:49,  8.18it/s]


  9%|███████▌                                                                       | 432/4550 [00:49<07:22,  9.30it/s]


...

100%|██████████████████████████████████████████████████████████████████████████████| 4550/4550 [07:53<00:00,  9.61it/s]

 47%|████████████████████████████████████▌                                        | 2158/4550 [00:15<00:14, 159.54it/s]


 99%|███████████████████████████████████████████████████████████████████████████▉ | 4488/4550 [00:34<00:00, 161.90it/s]


100%|█████████████████████████████████████████████████████████████████████████████| 4550/4550 [00:34<00:00, 130.21it/s]


{"file_list": ["C:\\Users\\mattm\\Documents\\CalPoly\\DATA 451\\Toyota\\data_transfer\\data-share\\structure\\SNL_18650_LFP_15C_0-100_0.5-1C_a_timeseries_CH01_structure.json"], "run_list": [0], "result_list": ["success"], "message_list": [{"comment": "", "error": ""}], "invalid_file_list": [], "mode": "events_off"}


c:\users\mattm\appdata\local\programs\python\python36\lib\site-packages\beep\featurize.py:1038: RuntimeWarning: All-NaN axis encountered
  X[17] = np.nanmin(IR_trend)


In [19]:
featurized

'{"file_list": ["C:\\\\Users\\\\mattm\\\\Documents\\\\CalPoly\\\\DATA 451\\\\Toyota\\\\data_transfer\\\\data-share\\\\structure\\\\SNL_18650_LFP_15C_0-100_0.5-1C_a_timeseries_CH01_structure.json", "C:\\\\Users\\\\mattm\\\\Documents\\\\CalPoly\\\\DATA 451\\\\Toyota\\\\data_transfer\\\\data-share\\\\structure\\\\SNL_18650_LFP_15C_0-100_0.5-1C_a_timeseries_CH01_structure.json", "C:\\\\Users\\\\mattm\\\\Documents\\\\CalPoly\\\\DATA 451\\\\Toyota\\\\data_transfer\\\\data-share\\\\structure\\\\SNL_18650_LFP_15C_0-100_0.5-1C_a_timeseries_CH01_structure.json", "C:\\\\Users\\\\mattm\\\\Documents\\\\CalPoly\\\\DATA 451\\\\Toyota\\\\data_transfer\\\\data-share\\\\structure\\\\SNL_18650_LFP_15C_0-100_0.5-1C_a_timeseries_CH01_structure.json", "C:\\\\Users\\\\mattm\\\\Documents\\\\CalPoly\\\\DATA 451\\\\Toyota\\\\data_transfer\\\\data-share\\\\features\\\\DeltaQFastCharge\\\\SNL_18650_LFP_15C_0-100.5-1C_a_timeseries_CH01_features_DeltaQFastCharge.json", "C:\\\\Users\\\\mattm\\\\Documents\\\\CalPoly\

In [4]:
from matplotlib import pyplot as plt
from monty.serialization import loadfn

In [5]:
processing_dir = os.environ.get("BEEP_PROCESSING_DIR", "data_transfer")
ftest = loadfn(os.path.join(processing_dir, 'data-share', 'features', 'DeltaQFastCharge', 'SNL_18650_LFP_15C_0-100.5-1C_a_timeseries_CH01_features_DeltaQFastCharge.json'))
ftest

In [24]:
ftest.X.columns

Index(['discharge_capacity_cycle_2', 'max_discharge_capacity_difference',
       'discharge_capacity_cycle_100',
       'integrated_time_temperature_cycles_1:100', 'charge_time_cycles_1:5',
       'abs_min_discharge_capacity_difference_cycles_2:100',
       'abs_mean_discharge_capacity_difference_cycles_2:100',
       'abs_variance_discharge_capacity_difference_cycles_2:100',
       'abs_skew_discharge_capacity_difference_cycles_2:100',
       'abs_kurtosis_discharge_capacity_difference_cycles_2:100',
       'abs_first_discharge_capacity_difference_cycles_2:100',
       'max_temperature_cycles_1:100', 'min_temperature_cycles_1:100',
       'slope_discharge_capacity_cycle_number_2:100',
       'intercept_discharge_capacity_cycle_number_2:100',
       'slope_discharge_capacity_cycle_number_91:100',
       'intercept_discharge_capacity_cycle_number_91:100',
       'min_internal_resistance_cycles_2:100', 'internal_resistance_cycle_2',
       'internal_resistance_difference_cycles_2:100',
 

In [25]:
variance_model = ["abs_variance_discharge_capacity_difference_cycles_2:100"]
variance_model_ind = [7]
discharge_model_ind = [5, 7, 8, 9, 0, 1]
full_model_ind = [5, 7, 13, 14, 0, 4, 3, 17, 19]

In [31]:
ftest.X.isna().T

0
discharge_capacity_cycle_2                          False
max_discharge_capacity_difference                   False
discharge_capacity_cycle_100                        False
integrated_time_temperature_cycles_1:100            False
charge_time_cycles_1:5                              False
abs_min_discharge_capacity_difference_cycles_2:100  False
abs_mean_discharge_capacity_difference_cycles_2...  False
abs_variance_discharge_capacity_difference_cycl...  False
abs_skew_discharge_capacity_difference_cycles_2...  False
abs_kurtosis_discharge_capacity_difference_cycl...  False
abs_first_discharge_capacity_difference_cycles_...  False
max_temperature_cycles_1:100                        False
min_temperature_cycles_1:100                        False
slope_discharge_capacity_cycle_number_2:100         False
intercept_discharge_capacity_cycle_number_2:100     False
slope_discharge_capacity_cycle_number_91:100        False
intercept_discharge_capacity_cycle_number_91:100    False
min_internal_resistance_cycles_2:100                 True
internal_resistance_cycle_2                          True
internal_resistance_difference_cycles_2:100          True
nominal_capacity_by_median                          False

In [6]:
ftest.X

discharge_capacity_cycle_2  max_discharge_capacity_difference  \
0                       1.032                              0.968   

   discharge_capacity_cycle_100  integrated_time_temperature_cycles_1:100  \
0                         1.032                                  378624.0   

   charge_time_cycles_1:5  abs_min_discharge_capacity_difference_cycles_2:100  \
0                  5760.0                                          -0.446806    

   abs_mean_discharge_capacity_difference_cycles_2:100  \
0                                          -2.742859     

   abs_variance_discharge_capacity_difference_cycles_2:100  \
0                                          -3.166992         

   abs_skew_discharge_capacity_difference_cycles_2:100  \
0                                           0.584775     

   abs_kurtosis_discharge_capacity_difference_cycles_2:100  ...  \
0                                           1.867028        ...   

   max_temperature_cycles_1:100  min_temperature_cycles_1:100  \
0                          20.0                          20.0   

   slope_discharge_capacity_cycle_number_2:100  \
0                                    -0.000572   

   intercept_discharge_capacity_cycle_number_2:100  \
0                                         1.071129   

   slope_discharge_capacity_cycle_number_91:100  \
0                                  1.217792e-17   

   intercept_discharge_capacity_cycle_number_91:100  \
0                                             1.032   

   min_internal_resistance_cycles_2:100  internal_resistance_cycle_2  \
0                                   NaN                          NaN   

   internal_resistance_difference_cycles_2:100  nominal_capacity_by_median  
0                                          NaN                       1.033  

[1 rows x 21 columns]